# Using the **Rcpp** package to access **c++** code from within **R**

## Background

**Rcpp** is an **R** package designed to automate many parts of the (quite complicated) process of accessing methods implemented in **c++** from within an **R** session (or indeed, an **R** package - see later section). To be able to use **Rcpp** the **Rcpp** package has to be installed. The **Rcpp** package is hosted on CRAN and can be installed using  

```c++
R> install.packages("Rcpp")
```

## Using the **sourceCpp** function

Perhaps the easiest way to see how **c++** can be added to **R** is via a simple example. To this end, the following c++ code will be added to R using the **sourceCpp** function which is provided by the **Rcpp** package.

### Preparing your **c++** code

```c++
#include <string>

std::string example_1(const std::string& arg) 
{
   std::string message {"hello"};
   return message + " " + arg;
}
```

To embed this function in **R** using **Rcpp**, some additional "boiler plate" code has to be added. 

```c++
#include "Rcpp.h"
using namespace Rcpp;

#include <string>

std::string example_1(const std::string& arg) 
{
   std::string message {"hello"};
   return message + " " + arg;
}

RCPP_MODULE(stor601) 
{
function("rcpp_example_1", &example_1);
}
```

The first addition

```c++
#include "Rcpp.h"
using namespace Rcpp;
```

imports the c++ code provided by the **Rcpp** package that will expose your function to **R** and, perhaps more significantly, "marshalls" data between **R** and **c++** (more on this later). 


The second addition

```c++
RCPP_MODULE(stor601) 
{
function("rcpp_example_1", &example_1);
}
```

creates an **Rcpp** module which contains your c++ method within an R session. Each module (you can have more than one) has a name, in this case **stor601**. The module definition indicates which function you want to expose to **R**, in this case **example_1**, and the name you want to give this function for use in **R**, in this example, **rcpp_example_1**  (this may be the same or different to the functions name in **c++**). 

### Adding your code to R

Perhaps the easiest (but maybe not the most effective) way of adding your (augmented) **c++** code to **R** is demonstrated in the example **R** session below.

In [5]:
library(Rcpp) # load the Rcpp package

# write your code into a string
cpp_code <- '
#include "Rcpp.h"
using namespace Rcpp;

#include <string>

std::string example_1(const std::string& arg) 
{
   std::string message {"hello"};
   return message + " " + arg;
}

RCPP_MODULE(stor601) 
{
function("rcpp_example_1", &example_1);
}
'

# add your code to R
sourceCpp(code = cpp_code)

# test your code
rcpp_example_1("world")


[1] "hello world"

Voila !! **c++** in **R** !!!

There are three key things to notice in this example.

1. The **c++** code has been "wrapped" as a string in **R**
2. the **sourceCpp** function takes this string as an argument.
3. The **c++** function becomes available in **R** (using the name you provided in the module definition).

### Adding c++ code to R from a source code file

Thus far, the **sourceCpp** function from the **Rcpp** package has been used to process c++ written into a string variable within an **R** session. This is useful, but can soon become inconvenient. Alternatively, th **c++** code can be saved in a file and the name of this file provided as an argument to the **sourceCpp** function. For instance, the example from section 1 could be saved into a file **example_1.cpp**, in which case, it can be added to **R** using **sourceCpp** as follows.

```R
sourceCpp(file="example_1.cpp")
```

## Controlling the c++ version

The **sourceCpp** function might not be configured to use a version of **c++** which is appropriate for your code (i.e. an older version than is required). The version of **c++** which **sourceCpp** uses can be set by adding the following to your augmented **c++** code.

```c++
// [[Rcpp::plugins("cpp17")]]
```

It needs to be placed after including the **Rcpp** header file. For example

```c++
#include "Rcpp.h"
using namespace Rcpp;

// [[Rcpp::plugins("cpp17")]]

#include <string>

std::string example_1(const std::string& arg) 
{
   std::string message {"hello"};
   return message + " " + arg;
}

RCPP_MODULE(stor601) 
{
function("rcpp_example_1", &example_1);
}
```